In [3]:
import pandas as pd
import folium
import matplotlib.pyplot as plt
plt.style.use('ggplot')
%matplotlib inline

In [4]:
def fix_section(d):
    d = str(d)
    if len(d)==1:
        return '0{0}'.format(d)
    else:
        return str(d)

In [7]:
df = pd.read_pickle('data/new.pickle')
df.head()
data = df.groupby('TRS').size().reset_index().rename(columns={0:'count'})
data.head()



df = pd.read_csv('data/PLSS_Sections.csv',dtype=object)
df['section']=df.apply(lambda x: fix_section(x['section']),axis=1)
df['TRS']=df['township'] + df['range'] + df['section'].astype(str)
df.head()
data_df = pd.merge(df[['TRS']],data[['TRS','count']],how='left',on='TRS').fillna(0)
data_df['count']=data_df['count'].astype(int)
data_df.to_csv('data/counts.csv',index=False)
set_mx=6
while data_df['count'].max() > set_mx:
    mx = data_df['count'].max()
    data_df.loc[data_df['count']==mx,'count']=set_mx
data_df.head()

TRS  count
0  01N61W01      5
1  01N61W02      2
2  01N61W03      2
3  01N61W04      6
4  01N61W05      6

In [28]:
df = pd.read_pickle('data/all_data.pickle')
df.head()

import json
with open('years.json') as f:
    years = json.load(f)['years']
    
def fix_years(s):
    for year in years:
        if year in s:
            return year
df['years']=df.apply(lambda x: fix_years(x['years']),axis=1)

conv={u'5':5, 
      u'4':4, 
      u'1':1, 
      u'one':1, 
      None:None,
      u'ten':10,
      u'3':3,
      u'2':2,
      u'five':5,
      u'three':3, 
      u'6':6, 
      u'two':2, 
      u'7':7, 
      u'9':9,
      u'8':8,
      u'twenty':20}
df['years']=df.apply(lambda x: conv[x['years']],axis=1)
df.to_pickle('data/all_')

doc                                         clean_text  \
0  DOC100S101_0  paid up oil and gas lease pages 1 of 2 3 8 6 7...   
1  DOC100S102_0  e e n ar o k o n a in 20 m paid up re 9 9 6 pa...   
2  DOC100S103_0  paid up oil and gas lease produce r s 8 8 3 8 ...   
3  DOC100S104_0  paid up oil and gas lease produce r s 8 8 r o ...   
4  DOC100S105_0  paid up oil and gas lease 3 8 6 7 9 2 5 08 22 ...   

                                          legal_text  years   town   range  \
0  section 11 township 5 north range 66 west more...    5.0  [[5]]  [[66]]   
1  section 11 township 5 north range 66 west more...    5.0  [[5]]  [[66]]   
2  section 14 township 5 north range 66 west more...    5.0  [[5]]  [[66]]   
3  section 3 township 5 north range 66 west more ...    4.0  [[5]]  [[66]]   
4  section 11 township 5 north range 66 west more...    5.0  [[5]]  [[66]]   

  section  
0  [[11]]  
1  [[11]]  
2  [[14]]  
3   [[3]]  
4  [[11]]

In [149]:
WELD_COORDINATES = (40.5, -104.41)
parcel_geo = 'geojsonfiles/PLSS_Sections.json'

weldmap = folium.Map(location=WELD_COORDINATES, zoom_start=9,tiles='Stamen Toner')
weldmap.choropleth(geo_path=parcel_geo, 
                   data=data_df,
                   data_out = 'weldagg.json',
                   columns=['TRS','count'],
                   threshold_scale=[1, 2,3,4,5,6],
                   key_on='feature.properties.TRS',
                   fill_color = 'YlOrRd',
                   fill_opacity=0.5)
# threshold_scale=[1, 5, 10, 15, 100,1500]
weldmap

In [107]:
import json
with open('geojsonfiles/PLSS_Sections.json') as f:
    jdata = json.load(f)

In [63]:
jdata['features'][0]['properties']

{u'AREA': 27940878.194,
 u'ASSRCODE': u'1481',
 u'PERIMETER': 42290.3486,
 u'RANGE': u'61W',
 u'Range2': u'61',
 u'SECTION': 1,
 u'Section2': u'1',
 u'Shape_Area': 27940878.4731,
 u'Shape_Leng': 21143.533171,
 u'TOWNRANGE': u'01N61W',
 u'TOWNSHIP': u'01N',
 u'TRS': u'01N61W01',
 u'TRS2': u'1 1 61',
 u'Township2': u'1'}

In [65]:
jdata['features']

[{u'geometry': {u'coordinates': [[[-104.15986373389951, 40.07332433968607],
     [-104.16458758617664, 40.073276525877596],
     [-104.16931131399946, 40.07322878760831],
     [-104.16928057235272, 40.076845810488976],
     [-104.169249824527, 40.08046292092534],
     [-104.16922079581562, 40.08408274374242],
     [-104.16919079080188, 40.08781112296926],
     [-104.16448767689869, 40.0878364760979],
     [-104.15978444456148, 40.08786181735049],
     [-104.15508132594427, 40.08788714851698],
     [-104.1503780888712, 40.087912467797885],
     [-104.15038446727571, 40.084289426818906],
     [-104.15039083971814, 40.0806664733407],
     [-104.15040354771206, 40.07704311405609],
     [-104.1504162490712, 40.07341984229988],
     [-104.15513999511894, 40.07337205254321],
     [-104.15986373389951, 40.07332433968607]]],
   u'type': u'Polygon'},
  u'properties': {u'AREA': 27940878.194,
   u'ASSRCODE': u'1481',
   u'PERIMETER': 42290.3486,
   u'RANGE': u'61W',
   u'Range2': u'61',
   u'SECTI

In [43]:
df = pd.read_csv('data/clean_weld_docs.csv')
df.loc[df['section']=='11121314','section']= '11,12,13,14'
df.loc[df['section']=='26,28 SE4','section']='26,28'
df.loc[df['section']=='2,2','section']='02'
df.loc[df['section']=='8,8','section']='08'
df.loc[df['section']=='S8','section']='08'
df.loc[df['section']=='126','section']='12'
df.loc[df['section']=='3334','section']='33,34'
df.loc[df['section']=='2526','section']='25,26'
df.loc[df['section']=='1617','section']='16,17'
df.loc[df['section']=='1819','section']='18,19'
df.loc[df['section']=='56','section']='5,6'

pd.unique(df['section'])

new = pd.DataFrame()
temp = pd.DataFrame()
options = set()
for i,r in df.iterrows():
    secs = r['section']
    if type(secs)==str:
        secs = secs.split(',')
        for sec in secs:
            r['section']=sec
            temp=temp.append(r,ignore_index=True)
    else:
        temp=temp.append(r,ignore_index=True)
    
    if i % 1000 == 0:
        print i
        new = new.append(temp,ignore_index=True)
        temp = pd.DataFrame()
    

0
1000
2000
3000
4000
5000
6000
7000
8000
9000
10000
11000
12000
13000
14000
15000
16000
17000
18000
19000
20000
21000
22000
23000
24000
25000
26000
27000
28000
29000
30000
31000
32000
33000
34000
35000
36000
37000
38000
39000
40000
41000
42000
43000
44000
45000
46000
47000
48000
49000
50000
